In [1]:
import json
import ast
from datetime import datetime as dt
import datetime

import pandas as pd
import plotly.express as px


In [2]:
rst = []
with open("file.txt",'r') as f:
    rst = f.read()

In [3]:
rsts = rst.split(",\n")

In [4]:
dicts = []
err_cnt = 0
for _rst in rsts :
    try:
        _dict = ast.literal_eval(_rst)
#         _dict['write_time'] = dt.strptime(_dict['write_time'][:-2],"%Y%m%d%H%M%S%f")
        _dict['write_time'] = dt.fromtimestamp(int(_dict['write_time'][12:]))
        dicts.append(_dict)
    except Exception as e:
#         print(e)
        err_cnt+=1
print(err_cnt)

1


### Raw

In [5]:
df= pd.DataFrame(dicts)
df  = df.reset_index()

In [6]:
df.loc[:,'concentration'] = df.loc[:,'concentration'] #*0.2831685

In [37]:
df.loc[:,'concentration_ma'] = df.loc[:,'concentration'].rolling(20).mean() #/1000

In [38]:
fig = px.line(df, x='write_time', y="concentration_ma")
fig.show()

### By date

In [39]:
dfbyDate = df.set_index('write_time')

In [40]:
dfbyDate.loc[:,'time'] =dfbyDate.index.round("30S").strftime("%H:%M.%S")
dfbyDate.loc[:,'date'] =dfbyDate.index.strftime("%m/%d")

In [41]:
dfbyDate = dfbyDate.sort_values(["time"])

In [42]:
fig = px.line(dfbyDate, x='time', y="concentration_ma",color='date')
fig.show()

In [44]:
import plotly.graph_objects as go

# Create traces
fig = go.Figure()
ls_time = sorted(list(set(dfbyDate.time)))
ls_date = sorted(list(set(dfbyDate.date)))
for _date in ls_date:
    fig.add_trace(go.Scatter(x=ls_time, y=dfbyDate.loc[dfbyDate["date"]==_date,"concentration_ma"],
                        mode='lines',
                        name=_date))
# Edit the layout
fig.update_layout(title='By time',
                   xaxis_title='Time',
                   yaxis_title='Concentration[pcs/ft3]')
fig.show()